In [1]:
!pip install keras_tuner

DEPRECATION: Python 2.7 reached the end of its life on January 1st, 2020. Please upgrade your Python as Python 2.7 is no longer maintained. pip 21.0 will drop support for Python 2.7 in January 2021. More details about Python 2 support in pip can be found at https://pip.pypa.io/en/latest/development/release-process/#python-2-support pip 21.0 will remove support for this functionality.
Defaulting to user installation because normal site-packages is not writeable
     |████████████████████████████████| 79 kB 6.6 MB/s  eta 0:00:01
    ERROR: Command errored out with exit status 1:
     command: /usr/bin/python2 -c 'import sys, setuptools, tokenize; sys.argv[0] = '"'"'/tmp/pip-install-Za4Qjl/keras-tuner/setup.py'"'"'; __file__='"'"'/tmp/pip-install-Za4Qjl/keras-tuner/setup.py'"'"';f=getattr(tokenize, '"'"'open'"'"', open)(__file__);code=f.read().replace('"'"'\r\n'"'"', '"'"'\n'"'"');f.close();exec(compile(code, __file__, '"'"'exec'"'"'))' egg_info --egg-base /tmp/pip-pip-egg-info-419j7n
   

In [5]:
import pandas as pd
import numpy as np
import random
import os
import matplotlib.pyplot as plt
import seaborn as sns
import tempfile

import io
from io import BytesIO
from urllib.parse import urlparse
import boto3

import tensorflow as tf
from tensorflow.keras.preprocessing.image import ImageDataGenerator, array_to_img, img_to_array, load_img
from PIL import ImageFile, Image
import warnings

import logging
from botocore.exceptions import ClientError

import time

from sklearn.model_selection import train_test_split
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Conv2D, MaxPooling2D, Flatten, Dense
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.losses import BinaryCrossentropy
from sklearn import ensemble
from sklearn.metrics import accuracy_score, confusion_matrix, ConfusionMatrixDisplay

In [4]:
num_threads = 16
tf.config.threading.set_intra_op_parallelism_threads(num_threads)
tf.config.threading.set_inter_op_parallelism_threads(num_threads)

In [6]:
# Initialize S3 client
s3_bucket = '207-images-labels'
session = boto3.Session(
#     aws_access_key_id='', #removed
#     aws_secret_access_key= '') #removed
client = session.client('s3')

## save baseline model to s3

In [7]:
def upload_file(file_name, bucket, object_name=None):
    """Upload a file to an S3 bucket

    :param file_name: File to upload
    :param bucket: Bucket to upload to
    :param object_name: S3 object name. If not specified then file_name is used
    :return: True if file was uploaded, else False
    """

    # If S3 object_name was not specified, use file_name
    if object_name is None:
        object_name = os.path.basename(file_name)

    try:
        response = client.upload_file(file_name, bucket, object_name)
    except ClientError as e:
        logging.error(e)
        return False
    return True

In [8]:
upload_file('model_baseline.h5', s3_bucket, object_name='models/model_baseline.h5')

True

## Preprocess images with 400,400 pixels

In [14]:
ImageFile.LOAD_TRUNCATED_IMAGES = True

In [15]:
warnings.simplefilter('ignore', Image.DecompressionBombWarning)
Image.MAX_IMAGE_PIXELS = None

In [4]:
def write_data_to_s3(bucket, key, data):
    np_bytes = io.BytesIO()
    np.save(np_bytes, data)
    np_bytes.seek(0)
    client.put_object(Bucket=bucket, Key=key, Body=np_bytes)

## load data from s3

In [11]:
images_prefix = 'train_400/pre1/images/'
labels_prefix = 'train_400/pre1/labels/'
bucket_name = '207-images-labels'

In [12]:
session_s3 = boto3.Session(
#    aws_access_key_id='', #removed
#    aws_secret_access_key='' #removed
)
s3 = session_s3.client('s3')

In [13]:
def list_s3(prefix):
    files = []
    continue_token = None
    while True:
        if continue_token:  
            response = s3.list_objects_v2(Bucket=bucket_name, Prefix=prefix, ContinuationToken=continue_token)
        else:
            response = s3.list_objects_v2(Bucket=bucket_name, Prefix=prefix)
        files.extend([item['Key'] for item in response.get('Contents', []) if item['Key'] != prefix])
        
        if response.get('IsTruncated'):
            continue_token = response.get('NextContinuationToken')
        else:
            break
    return files   

In [14]:
def load_s3_memmap(key):
    try:
        print(f"Loading file from S3: {key}")
        response = s3.get_object(Bucket=bucket_name, Key=key)
        file_content = BytesIO(response['Body'].read())
        
        # Save the content to a temporary file
        with tempfile.NamedTemporaryFile(delete=False) as tmp_file:
            tmp_file.write(file_content.read())
            temp_filename = tmp_file.name
        
        # Use numpy memmap to load the array
        data = np.load(temp_filename, mmap_mode='r')
        print(f"Loaded file: {key}, shape: {data.shape}")
        
        # Clean up the temporary file
        os.remove(temp_filename)
        
        return data
    except Exception as e:
        print(f"Error loading file {key}: {e}")
        return None

In [15]:
def subset_data(image_files, label_files, subset_ratio=0.5):
    total_files = len(image_files)
    subset_files = int(total_files * subset_ratio)
    
    indices = np.random.permutation(total_files)[:subset_files]
    
    subset_images = [image_files[i] for i in indices]
    subset_labels = [label_files[i] for i in indices]
    
    return subset_images, subset_labels

In [16]:
def s3_data_generator(image_keys, label_keys):
    skipped_count = 0  # Counter for skipped images
    skipped_files = []  # List to keep track of skipped file pairs

    for image_key, label_key in zip(image_keys, label_keys):
        try:
            images = load_s3_memmap(image_key)
            labels = load_s3_memmap(label_key)
        except Exception as e:
            print(f"Error loading file pair: {image_key}, {label_key} - {e}")
            skipped_files.append((image_key, label_key, e))
            skipped_count += 1
            continue  # Skip this pair if there's an error

        if images is None or labels is None:
            print(f"Skipping file pair: {image_key}, {label_key}")
            skipped_files.append((image_key, label_key, "Loaded None"))
            skipped_count += 1
            continue  # Skip this pair if there's an error

        # Ensure images and labels have the correct shape
        if images.ndim == 5 and images.shape[0] == 1:
            images = np.squeeze(images, axis=0)  # Remove the extra dimension

        if labels.ndim == 3 and labels.shape[0] == 1:
            labels = np.squeeze(labels, axis=0)  # Remove the extra dimension

        print(f"Loaded image batch: {image_key}, shape: {images.shape}")
        print(f"Loaded label batch: {label_key}, shape: {labels.shape}")

        # Yield each image and label individually
        for img, lbl in zip(images, labels):
            yield img, lbl

    print(f"Total skipped images: {skipped_count}")
    if skipped_files:
        print("Skipped file pairs and errors:")
        for image_key, label_key, error in skipped_files:
            print(f"Image: {image_key}, Label: {label_key}, Error: {error}")

In [14]:
image_files = list_s3(images_prefix)
label_files = list_s3(labels_prefix)
print(f'Total image files: {len(image_files)}')
print(f'Total label files: {len(label_files)}')

Total image files: 3865
Total label files: 3865


In [15]:
subset_images, subset_labels = subset_data(image_files, label_files, subset_ratio=0.1)
print(f'Subset image files: {len(subset_images)}')
print(f'Subset label files: {len(subset_labels)}')

Subset image files: 386
Subset label files: 386


In [16]:
shuffled_indices = np.random.permutation(len(subset_images))
subset_images = [subset_images[i] for i in shuffled_indices]
subset_labels = [subset_labels[i] for i in shuffled_indices]

In [17]:
sample_image = load_s3_memmap(subset_images[0])
sample_label = load_s3_memmap(subset_labels[0])
image_shape = sample_image.shape
label_shape = sample_label.shape

Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_3030_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_3030_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_400_pixels_batch_3030_lbls.npy
Loaded file: train_400/pre1/labels/img_numpy_train_400_pixels_batch_3030_lbls.npy, shape: (20,)


In [18]:
X_train, X_temp, y_train, y_temp = train_test_split(subset_images, subset_labels, test_size=0.4, random_state=42)
X_val, X_test, y_val, y_test = train_test_split(X_temp, y_temp, test_size=0.5, random_state=42)

In [19]:
print(f'length of X_train: {len(X_train)}')
print(f'length of y_train: {len(y_train)}')

length of X_train: 231
length of y_train: 231


In [20]:
batch_size = 20
train_set = tf.data.Dataset.from_generator(
    lambda: s3_data_generator(X_train, y_train),
    output_signature=(
        tf.TensorSpec(shape=(400,400,3), dtype=tf.float32),
        tf.TensorSpec(shape=(), dtype=tf.float32)
    )
).batch(2).shuffle(buffer_size=20).prefetch(buffer_size=tf.data.AUTOTUNE)

In [21]:
val_set = tf.data.Dataset.from_generator(
    lambda: s3_data_generator(X_val, y_val),
    output_signature=(
        tf.TensorSpec(shape=(400,400,3), dtype=tf.float32),
        tf.TensorSpec(shape=(), dtype=tf.float32)
    )
).batch(2).shuffle(buffer_size=20).prefetch(buffer_size=tf.data.AUTOTUNE)

In [22]:
test_set = tf.data.Dataset.from_generator(
    lambda: s3_data_generator(X_test, y_test),
    output_signature=(
        tf.TensorSpec(shape=(400,400,3), dtype=tf.float32),
        tf.TensorSpec(shape=(), dtype=tf.float32)
    )
).batch(2).shuffle(buffer_size=20).prefetch(buffer_size=tf.data.AUTOTUNE)

In [29]:
tuner = tune_model()
tuner.search(
    train_set, 
    validation_data=val_set,
    epochs=2,
    batch_size=32
)

Reloading Tuner from tuner_results/cnn_tuning/tuner0.json

Search: Running Trial #3

Value             |Best Value So Far |Hyperparameter
96                |32                |filters_1
5                 |5                 |kernel_size
4                 |3                 |pool_size_1
96                |64                |filters_2
5                 |5                 |kernel_size_2
3                 |3                 |pool_size_2
384               |256               |units
0.0001            |1e-05             |learning_rate

Epoch 1/2
Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_3417_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_3417_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_400_pixels_batch_3417_lbls.npy
Loaded file: train_400/pre1/labels/img_numpy_train_400_pixels_batch_3417_lbls.npy, shape: (20,)
Loaded image batch: train_400/pre1/images/img_numpy_train_400_pixels_ba

2024-08-05 00:36:21.883301: I tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence
	 [[{{node IteratorGetNext}}]]
/usr/local/lib/python3.10/contextlib.py:153: UserWarning: Your input ran out of data; interrupting training. Make sure that your dataset or generator can generate at least `steps_per_epoch * epochs` batches. You may need to use the `.repeat()` function when building your dataset.
  self.gen.throw(typ, value, traceback)


Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_3355_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_400_pixels_batch_3355_lbls.npy
Loaded file: train_400/pre1/labels/img_numpy_train_400_pixels_batch_3355_lbls.npy, shape: (20,)
Loaded image batch: train_400/pre1/images/img_numpy_train_400_pixels_batch_3355_imgs.npy, shape: (20, 400, 400, 3)
Loaded label batch: train_400/pre1/labels/img_numpy_train_400_pixels_batch_3355_lbls.npy, shape: (20,)
Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_1645_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_1645_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1645_lbls.npy
Loaded file: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1645_lbls.npy, shape: (20,)
Loaded image batch: train_400/pre1/images/img_numpy_train_400_pixels_batch_1645_imgs.npy, shape: (20,

2024-08-05 00:41:28.787136: I tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence
	 [[{{node IteratorGetNext}}]]


12490/12490 ━━━━━━━━━━━━━━━━━━━━ 5434s 435ms/step - accuracy: 0.6860 - loss: 0.5829 - val_accuracy: 0.7939 - val_loss: 0.4606
Epoch 2/2
Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_3417_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_3417_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_400_pixels_batch_3417_lbls.npy
Loaded file: train_400/pre1/labels/img_numpy_train_400_pixels_batch_3417_lbls.npy, shape: (20,)
Loaded image batch: train_400/pre1/images/img_numpy_train_400_pixels_batch_3417_imgs.npy, shape: (20, 400, 400, 3)
Loaded label batch: train_400/pre1/labels/img_numpy_train_400_pixels_batch_3417_lbls.npy, shape: (20,)
Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_3404_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_3404_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_4

2024-08-05 02:11:45.009085: I tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence
	 [[{{node IteratorGetNext}}]]


Epoch 1/2
Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_3417_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_3417_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_400_pixels_batch_3417_lbls.npy
Loaded file: train_400/pre1/labels/img_numpy_train_400_pixels_batch_3417_lbls.npy, shape: (20,)
Loaded image batch: train_400/pre1/images/img_numpy_train_400_pixels_batch_3417_imgs.npy, shape: (20, 400, 400, 3)
Loaded label batch: train_400/pre1/labels/img_numpy_train_400_pixels_batch_3417_lbls.npy, shape: (20,)
Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_3404_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_3404_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_400_pixels_batch_3404_lbls.npy
Loaded file: train_400/pre1/labels/img_numpy_train_400_pixels_batch_3404_lbls.npy, shape: (20,)


KeyboardInterrupt: 

In [23]:
tuner2 = tune_model()
tuner2.search(
    train_set, 
    validation_data=val_set,
    epochs=2,
    batch_size=32
)

Trial 10 Complete [01h 00m 57s]
val_accuracy: 0.7048192918300629

Best val_accuracy So Far: 0.7611445784568787
Total elapsed time: 21h 09m 03s

Search: Running Trial #11

Value             |Best Value So Far |Hyperparameter
48                |112               |filters_1
5                 |3                 |kernel_size
3                 |3                 |pool_size_1
96                |160               |filters_2
5                 |3                 |kernel_size_2
3                 |3                 |pool_size_2
384               |256               |units
0.0001            |0.0001            |learning_rate

Epoch 1/2
Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_1499_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_1499_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1499_lbls.npy
Loaded file: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1499_lbls.npy

KeyboardInterrupt: 

In [32]:
best_hps=tuner2.get_best_hyperparameters(num_trials=1)[0]

In [33]:
print(f"""
filters_1: {best_hps.get('filters_1')} 
kernel_size: {best_hps.get('kernel_size')} 
filters_2: {best_hps.get('filters_2')} 
kernel_size_2: {best_hps.get('kernel_size_2')} 
pool_size_2: {best_hps.get('pool_size_2')} 
units: {best_hps.get('units')} 
learning rate: {best_hps.get('learning_rate')}
""")


filters_1: 112 
kernel_size: 3 
filters_2: 160 
kernel_size_2: 3 
pool_size_2: 3 
units: 256 
learning rate: 0.0001



## train model on all of training set

In [17]:
train_images_prefix = 'train_400/pre1/images/'
train_labels_prefix = 'train_400/pre1/labels/'
test_images_prefix = 'test_400/pre1/labels/'
test_labels_prefix = 'test_400/pre1/labels/'

In [18]:
train_image_files = list_s3(train_images_prefix)
train_label_files = list_s3(train_labels_prefix)
print(f'Total image files: {len(train_image_files)}')
print(f'Total label files: {len(train_label_files)}')

Total image files: 3865
Total label files: 3865


In [19]:
test_image_files = list_s3(test_images_prefix)
test_label_files = list_s3(test_labels_prefix)
print(f'Total image files: {len(test_image_files)}')
print(f'Total label files: {len(test_label_files)}')

Total image files: 300
Total label files: 300


In [20]:
batch_size = 20
train_set_400 = tf.data.Dataset.from_generator(
    lambda: s3_data_generator(train_image_files, train_label_files),
    output_signature=(
        tf.TensorSpec(shape=(400,400,3), dtype=tf.float32),
        tf.TensorSpec(shape=(), dtype=tf.float32)
    )
).batch(2).shuffle(buffer_size=20).prefetch(buffer_size=tf.data.AUTOTUNE)

In [21]:
test_set_400 = tf.data.Dataset.from_generator(
    lambda: s3_data_generator(test_image_files, test_label_files),
    output_signature=(
        tf.TensorSpec(shape=(400,400,3), dtype=tf.float32),
        tf.TensorSpec(shape=(), dtype=tf.float32)
    )
).batch(2).shuffle(buffer_size=20).prefetch(buffer_size=tf.data.AUTOTUNE)

In [22]:
model_400 = Sequential([
    Conv2D(64, (4, 4), activation='relu', input_shape=(400, 400, 3)),
    MaxPooling2D((2, 2)),
    Flatten(),
    Dense(32, activation='relu'),
    Dense(24, activation='relu'),
    Dense(1, activation='sigmoid')  # Binary classification
])
model_400.compile(optimizer='adam',
              loss='binary_crossentropy',
              metrics=['accuracy'])
model_400.summary()

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
conv2d (Conv2D)              (None, 397, 397, 64)      3136      
_________________________________________________________________
max_pooling2d (MaxPooling2D) (None, 198, 198, 64)      0         
_________________________________________________________________
flatten (Flatten)            (None, 2509056)           0         
_________________________________________________________________
dense (Dense)                (None, 32)                80289824  
_________________________________________________________________
dense_1 (Dense)              (None, 24)                792       
_________________________________________________________________
dense_2 (Dense)              (None, 1)                 25        
Total params: 80,293,777
Trainable params: 80,293,777
Non-trainable params: 0
____________________________________________

In [ ]:
history = model_400.fit(train_set_400, epochs=1, verbose=4)

Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_1269_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_1269_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1269_lbls.npy
Loaded file: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1269_lbls.npy, shape: (20,)
Loaded image batch: train_400/pre1/images/img_numpy_train_400_pixels_batch_1269_imgs.npy, shape: (20, 400, 400, 3)
Loaded label batch: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1269_lbls.npy, shape: (20,)
Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_1270_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_1270_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1270_lbls.npy
Loaded file: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1270_lbls.npy, shape: (20,)
Loaded ima

Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_1282_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_1282_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1282_lbls.npy
Loaded file: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1282_lbls.npy, shape: (20,)
Loaded image batch: train_400/pre1/images/img_numpy_train_400_pixels_batch_1282_imgs.npy, shape: (20, 400, 400, 3)
Loaded label batch: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1282_lbls.npy, shape: (20,)
Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_1283_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_1283_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1283_lbls.npy
Loaded file: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1283_lbls.npy, shape: (20,)
Loaded ima

Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_1295_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_1295_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1295_lbls.npy
Loaded file: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1295_lbls.npy, shape: (20,)
Loaded image batch: train_400/pre1/images/img_numpy_train_400_pixels_batch_1295_imgs.npy, shape: (20, 400, 400, 3)
Loaded label batch: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1295_lbls.npy, shape: (20,)
Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_1296_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_1296_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1296_lbls.npy
Loaded file: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1296_lbls.npy, shape: (20,)
Loaded ima

Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_1308_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_1308_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1308_lbls.npy
Loaded file: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1308_lbls.npy, shape: (20,)
Loaded image batch: train_400/pre1/images/img_numpy_train_400_pixels_batch_1308_imgs.npy, shape: (20, 400, 400, 3)
Loaded label batch: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1308_lbls.npy, shape: (20,)
Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_1309_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_1309_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1309_lbls.npy
Loaded file: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1309_lbls.npy, shape: (20,)
Loaded ima

Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_1320_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_1320_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1320_lbls.npy
Loaded file: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1320_lbls.npy, shape: (20,)
Loaded image batch: train_400/pre1/images/img_numpy_train_400_pixels_batch_1320_imgs.npy, shape: (20, 400, 400, 3)
Loaded label batch: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1320_lbls.npy, shape: (20,)
Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_1321_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_1321_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1321_lbls.npy
Loaded file: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1321_lbls.npy, shape: (20,)
Loaded ima

...

Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_1522_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_1522_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1522_lbls.npy
Loaded file: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1522_lbls.npy, shape: (20,)
Loaded image batch: train_400/pre1/images/img_numpy_train_400_pixels_batch_1522_imgs.npy, shape: (20, 400, 400, 3)
Loaded label batch: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1522_lbls.npy, shape: (20,)
Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_1523_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_1523_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1523_lbls.npy
Loaded file: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1523_lbls.npy, shape: (20,)
Loaded ima

Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_1535_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_1535_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1535_lbls.npy
Loaded file: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1535_lbls.npy, shape: (20,)
Loaded image batch: train_400/pre1/images/img_numpy_train_400_pixels_batch_1535_imgs.npy, shape: (20, 400, 400, 3)
Loaded label batch: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1535_lbls.npy, shape: (20,)
Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_1536_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_1536_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1536_lbls.npy
Loaded file: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1536_lbls.npy, shape: (20,)
Loaded ima

Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_1548_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_1548_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1548_lbls.npy
Loaded file: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1548_lbls.npy, shape: (20,)
Loaded image batch: train_400/pre1/images/img_numpy_train_400_pixels_batch_1548_imgs.npy, shape: (20, 400, 400, 3)
Loaded label batch: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1548_lbls.npy, shape: (20,)
Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_1549_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_1549_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1549_lbls.npy
Loaded file: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1549_lbls.npy, shape: (20,)
Loaded ima

Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_1560_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_1560_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1560_lbls.npy
Loaded file: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1560_lbls.npy, shape: (20,)
Loaded image batch: train_400/pre1/images/img_numpy_train_400_pixels_batch_1560_imgs.npy, shape: (20, 400, 400, 3)
Loaded label batch: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1560_lbls.npy, shape: (20,)
Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_1561_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_1561_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1561_lbls.npy
Loaded file: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1561_lbls.npy, shape: (20,)
Loaded ima

Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_1573_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_1573_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1573_lbls.npy
Loaded file: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1573_lbls.npy, shape: (20,)
Loaded image batch: train_400/pre1/images/img_numpy_train_400_pixels_batch_1573_imgs.npy, shape: (20, 400, 400, 3)
Loaded label batch: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1573_lbls.npy, shape: (20,)
Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_1574_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_1574_imgs.npy, shape: (20, 400, 400, 3)
Loading file from S3: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1574_lbls.npy
Loaded file: train_400/pre1/labels/img_numpy_train_400_pixels_batch_1574_lbls.npy, shape: (20,)
Loaded ima

In [ ]:
model_400.save('baseline_400.h5')

In [39]:
images = load_s3_memmap('train_400/pre1/images/img_numpy_train_400_pixels_batch_1277_imgs.npy')
model_400.predict(images)
print(images[0])

Loading file from S3: train_400/pre1/images/img_numpy_train_400_pixels_batch_1277_imgs.npy
Loaded file: train_400/pre1/images/img_numpy_train_400_pixels_batch_1277_imgs.npy, shape: (20, 400, 400, 3)
[[[0.9024103  0.9024103  0.9024103 ]
  [0.9024103  0.9024103  0.9024103 ]
  [0.9024103  0.9024103  0.9024103 ]
  ...
  [0.78459024 0.78459024 0.78459024]
  [0.78459024 0.78459024 0.78459024]
  [0.7809084  0.7809084  0.7809084 ]]

 [[0.9024103  0.9024103  0.9024103 ]
  [0.9024103  0.9024103  0.9024103 ]
  [0.9024103  0.9024103  0.9024103 ]
  ...
  [0.78459024 0.78459024 0.78459024]
  [0.7809084  0.7809084  0.7809084 ]
  [0.77722645 0.77722645 0.77722645]]

 [[0.9024103  0.9024103  0.9024103 ]
  [0.9024103  0.9024103  0.9024103 ]
  [0.9024103  0.9024103  0.9024103 ]
  ...
  [0.7735446  0.7735446  0.7735446 ]
  [0.78459024 0.78459024 0.78459024]
  [0.7809084  0.7809084  0.7809084 ]]

 ...

 [[0.85454595 0.85454595 0.85454595]
  [0.8471822  0.8471822  0.8471822 ]
  [0.8471822  0.8471822  0.8471